# 实验3-3 LeNet模型定义和训练

实验目标：

* 初步掌握模型构建和训练


### 1. 定义网络

首先定义一个LeNet网络:

In [6]:
import torch
import torch.nn as nn  # 类
import torch.nn.functional as F  # 函数

class LeNet(nn.Module):
    def __init__(self):
        super().__init__()
        # 1 input image channel, 6 output channels, 5x5 square convolution
        # kernel
        self.conv1 = nn.Conv2d(1, 6, 5)  # 通道: 1 => 6, kernel size: 5
        self.conv2 = nn.Conv2d(6, 16, 5)
        # an affine operation: y = Wx + b
        self.fc1 = nn.Linear(16 * 5 * 5, 120)  # 5*5 from image dimension 
        self.fc2 = nn.Linear(120, 84)
        self.fc3 = nn.Linear(84, 10)

    def forward(self, x):
        ''' 定义网络前馈的过程，而其反向推导则基于此自动进行
        '''
        # Max pooling over a (2, 2) window
        x = F.max_pool2d(F.relu(self.conv1(x)), (2, 2))
        # If the size is a square, you can specify with a single number
        x = F.max_pool2d(F.relu(self.conv2(x)), 2)
        x = torch.flatten(x, 1) # flatten all dimensions except the batch dimension
        x = F.relu(self.fc1(x))
        x = F.relu(self.fc2(x))
        x = self.fc3(x)
        return x


net = LeNet()
print(net)

LeNet(
  (conv1): Conv2d(1, 6, kernel_size=(5, 5), stride=(1, 1))
  (conv2): Conv2d(6, 16, kernel_size=(5, 5), stride=(1, 1))
  (fc1): Linear(in_features=400, out_features=120, bias=True)
  (fc2): Linear(in_features=120, out_features=84, bias=True)
  (fc3): Linear(in_features=84, out_features=10, bias=True)
)


> 请回答：
> 1. 前文代码块中`nn.Conv2d`和`nn.Linear`分别是什么模块？
> 2. `nn.Conv2d`和`nn.Linear`在初始化时，其构造函数的参数是怎样的？

In [7]:
1. 卷积层和线性层
2.分别为:输入通道数量 输出通道数量 卷积核大小
         输入维度 输出维度

SyntaxError: invalid syntax (1425913863.py, line 1)

您只需要重新定义`nn.Module`类的`forward`成员函数（即前向传播），而无需定义`backward`成员函数（即反向传播）。在`forward`函数中，可以自由地使用任何张量运算。

这是因为，`autograd`计算图机制将自动化的定义`backward`成员函数。


### 2. 获取权重

在定义好神经网络（本例中即为`LeNet`）后，通过 `net.parameters()`成员函数可获取该网络中可学习的参数（又称权重）。

所获取的权重可以交给PyTorch利用梯度计算机制统一更新。

In [ ]:
params = list(net.parameters())
print(len(params))
print(params[0].size())  # conv1's .weight
#print(params)

10
torch.Size([6, 1, 5, 5])


### 3. 测试输入输出

让我们尝试一个随机的 32x32 输入。

注意：此网络`LeNet`的预期输入大小为 32x32。要将此网络用于MNIST 数据集，请将数据集中的图像大小调整为 32x32。



In [ ]:
input = torch.randn(1, 1, 32, 32)
out = net(input)
print(out)

tensor([[ 0.0719,  0.0145, -0.1102, -0.0903, -0.0850, -0.0460,  0.0280, -0.0440,
         -0.0256,  0.0834]], grad_fn=<AddmmBackward0>)


> 请回答：
> 1. 请在代码中测试，若输入不是(1, 1, 32, 32)尺寸的张量，会导致什么效果？

将所有参数的梯度缓存清零，并用伪真值（随机值）计算损失并反向传播（BP）。



In [ ]:
output = net(input)
target = torch.randn(10)  # a dummy target, for example
target = target.view(1, -1)  # make it the same shape as output
criterion = nn.MSELoss()

loss = criterion(output, target)
print(loss)

tensor(0.8519, grad_fn=<MseLossBackward0>)


至此，从`input`到`loss`计算过程，可以用如下计算图（computational graph）来表示：

    input -> conv2d -> relu -> maxpool2d -> conv2d -> relu -> maxpool2d
          -> flatten -> linear -> relu -> linear -> relu -> linear
          -> MSELoss
          -> loss

所以，当调用`loss.backward()`时, 整个计算图是可以求解导数的，即该网络中所有具有`requires_grad=True`属性的张量皆会计算其梯度，并保存于`.grad`属性之中。

### 4. 反向推导Backprop


要计算反向传播的梯度，我们所要做的就是调用`loss.backward()`成员函数。

但请注意，需要预先清除已有的权重梯度值，否则权重的梯度值将是若干次梯度反向传播的累积值。

现在我们将调用`loss.backward()`函数，并观察conv1的梯度的前后变化


In [ ]:
net.zero_grad()     # zeroes the gradient buffers of all parameters

print('conv1.bias.grad before backward')
print(net.conv1.bias.grad)

loss.backward()

print('conv1.bias.grad after backward')
print(net.conv1.bias.grad)

conv1.bias.grad before backward
None
conv1.bias.grad after backward
tensor([ 0.0115,  0.0092,  0.0135,  0.0001, -0.0111,  0.0149])


> 请回答：
> 1. 说明前文代码块中，conv1的梯度在`loss.backward()`执行前后变化。以及为什么会这样？

执行之后产生梯度值. 执行损失计算后梯度得到了更新

### 5. 更新权重

实际中最简单的权重优化原则，即为随机梯度下降Stochastic Gradient Descent (SGD)

     ``weight = weight - learning_rate * gradient``

以下Python代码来实现SGD功能：

```python
    learning_rate = 0.01
    for f in net.parameters():
        f.data.sub_(f.grad.data * learning_rate)
```

但是，当使用神经网络时，通常希望使用各种不同的权重优化规则，如SGD，Nesterov-SGD，Adam，RMSProp等。因此，前文所述代码在实际中并不常用。

为了实现这一点，需要用到PyTorch的包：`torch.optim`，其中实现所有这些方法。使用非常简单。


In [ ]:
import torch.optim as optim

# create your optimizer
optimizer = optim.SGD(net.parameters(), lr=0.01)

for i in range(10):
    # input = ...
    # in your training loop:
    optimizer.zero_grad()   # zero the gradient buffers
    output = net(input)
    loss = criterion(output, target)
    loss.backward()
    optimizer.step()    # Does the update

> 请回答：
> 1. 请结合实验结果，解释前文代码块中`for`循环内每行代码的功能。

分别为:
清空梯度数据
数据输入网络得到输出
计算损失值
反向传播
更新参数

### 6. 完整训练LeNet网络（可选）

参考 https://pytorch.org/tutorials/beginner/basics/quickstart_tutorial.html
    
> 在此执行一次完整的LeNet训练。给出实验代码和效果。